In [1]:
import numpy as np
import pandas as pd
import copy
import matplotlib.pyplot as plt
import requests
import math
import requests
from operator import itemgetter
from datetime import datetime
import time

# High Dividend Yield Stock Screening Criteria
# Market Capitalization > 2 B
# Dividend Yield > 3% < 10%######>1.5%
# Dividend 1 Year Change % > 2%
# Dividend 3 Year Average % > 2%
# Payout Ratio > 30 and < 60

# 安全股息筛选标准
# 市值 > 20 亿美元
# 股息收益率 > 1.5%
# 股息 1 年变化 % > 0%
# 股息 3 年平均百分比 > 0%
# 股息 5 年平均百分比 > 0%
# 主要交易所（非场外交易）的股票
# 支付比率 > 30 和 < 50
# 5 年平均销售额增长 > 4.5%


def high_div(symbols):

    api_key1 = '8a1cf9d14d53126b05c8a7636fe3d006'
    stocks = pd.DataFrame(columns = ['mktCap','price','symbol','volAvg','lastDiv'])
    #ticker = 'FAST'
    for ticker in symbols:
        try:
            bs =requests.get(f'https://financialmodelingprep.com/api/v3/profile/{ticker}?apikey={api_key1}').json()[0]
            stocks = stocks.append({'mktCap':bs['mktCap'],'price':bs['price'], 'symbol':bs['symbol'], 'volAvg':bs['volAvg'],'lastDiv':bs['lastDiv']}, ignore_index=True)
            stocks['dividend_yield'] = stocks['lastDiv']/stocks['price']
        except:
            pass
    stocks =stocks.set_index('symbol')
        
    
    api_key1 = '8a1cf9d14d53126b05c8a7636fe3d006'
    stocks1 = pd.DataFrame(columns = ['dividendYielPercentageTTM','payoutRatioTTM','symbol'])
    for ticker in symbols:
        try:
            bs =requests.get(f'https://financialmodelingprep.com/api/v3/ratios-ttm/{ticker}?apikey={api_key1}').json()[0]
            stocks1 = stocks1.append({'dividendYielPercentageTTM':bs['dividendYielPercentageTTM'],'payoutRatioTTM':bs['payoutRatioTTM'], 'symbol':ticker}, ignore_index=True)
        except:
            pass
    stocks1 =stocks1.set_index('symbol')        

    ############DIVIDEND ARE BASED ON YEARLY###############
    stocks2 = pd.DataFrame(columns = [ "fiveYDividendperShareGrowthPerShare", "threeYDividendperShareGrowthPerShare"])
    
    for ticker in symbols:
        try:
            bs =requests.get(f'https://financialmodelingprep.com/api/v3/financial-growth/{ticker}?apikey={api_key1}').json()[0]
            stocks2 = stocks2.append({"fiveYDividendperShareGrowthPerShare":bs["fiveYDividendperShareGrowthPerShare"],"threeYDividendperShareGrowthPerShare":bs["threeYDividendperShareGrowthPerShare"], 'symbol':ticker}, ignore_index=True)
    
        except:
            pass
    stocks2 =stocks2.set_index('symbol')             
    
    stocks1 = stocks1.sort_index()
    stocks2=stocks2.sort_index()
    stocks=stocks.sort_index()
    all_data = pd.concat([stocks, stocks2,stocks1], axis=1, join="inner")
    #  all_data 
    # data=stocks.merge(stocks1, left_index=True, right_index=True)
    # all_data = data.merge(stocks2,left_index=True, right_index=True)
    
   #all_data =all_data.dropna()

    div = pd.DataFrame()
    for ticker in symbols:
        try:
            bs =requests.get(f'https://financialmodelingprep.com/api/v3/historical-price-full/stock_dividend/{ticker}?apikey={api_key1}').json()['historical']
            dividend=pd.DataFrame(columns = ['date','dividend'])
            for i in range(len(bs)):
                dividend= dividend.append({'date':bs[i]['date'], 'dividend':bs[i]['dividend']}, ignore_index = True)
                
            dividend_data = pd.DataFrame(columns = ['date','dividend'])
            for i in range(1,len(dividend)):
                dividend_data =  dividend_data.append({'date':bs[i]['date'], 'dividend':bs[i]['dividend']}, ignore_index = True)
                if i >21:
                    break 
            
            
            div_data = pd.DataFrame(columns = ['date','dividendAvg'])
            for i in range(6):
                div_data=  div_data.append({'date': dividend_data['date'][ 4*i], 'dividendAvg':dividend_data['dividend'][ 4*i]},ignore_index = True)
            
            div_data ['dividendAvg'] =div_data['dividendAvg']*4
            avg_div3y = div_data.loc[1:3,'dividendAvg'].mean()
            avg_div5y =div_data.loc[1:5,'dividendAvg'].mean()
            one_yearchange = (div_data.loc[0,'dividendAvg']-div_data.loc[1,'dividendAvg'])/div_data.loc[1,'dividendAvg']
            dataa =pd.DataFrame(columns = ['symbol', 'avg_div3y','avgdiv5y', 'one_yearchange'])
            dataa = dataa.append({'symbol':ticker, 'avg_div3y':avg_div3y ,'avgdiv5y':avg_div5y,'one_yearchange':one_yearchange}, ignore_index = True)
            div =pd.concat([div,dataa], axis =0)
            
        except:
            pass
    div= div.set_index('symbol')
    #div =div.dropna()
    div = div.sort_index()
    
    all_data1 = pd.concat([ all_data ,div], axis=1, join="inner")
  #  all_data1 = all_data.merge(div,left_index=True, right_index=True)
    all_data1= all_data1.dropna()
        
    all_data1 = all_data1[all_data1['mktCap'] >2000000000]
    all_data1 =  all_data1[all_data1['dividend_yield'] >0.015]
    all_data1 =  all_data1[all_data1['one_yearchange'] >0.02]
    all_data1 =  all_data1[all_data1["avg_div3y"]>0]
    all_data1 =  all_data1[all_data1[ "avgdiv5y"]>0]
    all_data1 = all_data1[all_data1['payoutRatioTTM'] > 0.3] 
    all_data1 = all_data1[ all_data1['payoutRatioTTM'] <0.8]
    return all_data1

In [2]:
d =pd.read_csv(r'C:\Users\jizha\Desktop\seabridge_datapool1\stock_lists.csv' ) 
symbols = list(d['0']) 


In [5]:
n =3
high_dividend =pd.DataFrame()
groups = np.array_split(symbols, n)
import time
for group in groups:
    for ticker in group:
        hig_dividend = high_div(ticker)
    high_dividend = pd.concat([high_dividend,hig_dividend],axis =0)
    time.sleep(60)

InvalidIndexError: Reindexing only valid with uniquely valued Index objects

In [3]:
n = 3# number of groups
groups = np.array_split(symbols, n)
group1 = groups[0].tolist()
group2 = groups[1].tolist()
group3 = groups[2].tolist()
#group4 = groups[3].tolist()
#group5 = groups[4].tolist()


In [4]:
data1 =high_div(group1)

In [5]:
data1

mktCap    price    volAvg  lastDiv  dividend_yield  \
symbol                                                             
ADI      59657768960  161.750   3196826   2.6200        0.016198   
ADM      32941070336   58.960   2594607   1.4600        0.024763   
ADP      88163082240  207.190   1569558   3.7000        0.017858   
AEE      21493284864   84.105   1322273   2.1100        0.025088   
AEP      43862007808   87.680   2812652   3.6600        0.041743   
AIZ       9484730368  156.600    344977   2.6100        0.016667   
AMGN    140317573120  244.220   2607380   6.7200        0.027516   
AOS      11294497792   70.390   1040444   1.2800        0.018184   
APD      64435568640  291.150    849728   5.6800        0.019509   
ARE      29442344960  199.601    858609   4.3600        0.021844   
ATO      13162403840  100.640    757831   2.4500        0.024344   
BEN      14983436288   29.710   2784874   1.1100        0.037361   
BLK     132140711936  867.640    567306  15.5200        0.017888   
BX       82328674304  114.270   4116853   3.3900        0.029667   
CAG      16506403840   34.365   3358890   1.3510        0.039313   
CL       71247511552   84.220   3993455   1.7800        0.021135   
CLX      23030585344  185.175   1371085   5.6000        0.030242   
CMCSA   269225394176   58.600  15801195   0.9600        0.016382   
CMI      34357706752  235.000    980139   5.3610        0.022813   
CMS      18111512576   62.570   2506052   2.1210        0.033898   
CPB      13605475328   44.895   2518628   1.4600        0.032520   
CSCO    232413134848   55.150  18163585   1.4600        0.026473   
EMN      15250566144  111.870    714903   2.7300        0.024403   
ES       29665157120   86.370   1662641   2.3415        0.027110   
ETR      21038198784  104.845   1005339   3.7800        0.036053   
EVRG     15088126976   65.810   1220461   2.1100        0.032062   

        fiveYDividendperShareGrowthPerShare  \
symbol                                        
ADI                                0.527875   
ADM                                0.260184   
ADP                                0.739091   
AEE                                0.213845   
AEP                               -0.995334   
AIZ                                0.852022   
AMGN                               1.030657   
AOS                                1.535688   
APD                                0.582536   
ARE                                0.255625   
ATO                                0.464697   
BEN                                0.001657   
BLK                                0.670461   
BX                                -0.382037   
CAG                               -2.353265   
CL                                 0.170226   
CLX                                0.429321   
CMCSA                              0.867682   
CMI                                0.510039   
CMS                                0.410581   
CPB                                0.120600   
CSCO                               0.788641   
EMN                                0.652065   
ES                                 0.382140   
ETR                               -1.000000   
EVRG                               0.516378   

        threeYDividendperShareGrowthPerShare  dividendYielPercentageTTM  \
symbol                                                                    
ADI                                 0.396803                   1.619383   
ADM                                 0.110212                   2.475415   
ADP                                 0.535900                   1.785197   
AEE                                 0.132171                   2.508769   
AEP                                -0.995842                   4.174270   
AIZ                                 0.182241                   1.664966   
AMGN                                0.394397                   2.751617   
AOS                                 0.731493                   1.817665   
APD                                 0.3804

In [6]:
data2 =high_div(group2)

In [7]:
data2

mktCap    price    volAvg  lastDiv  dividend_yield  \
symbol                                                             
FMC      13725400064  106.500    785600   1.8800        0.017653   
GLW      34588930048   40.628   4365382   0.9200        0.022644   
GPC      18449143808  128.824    720223   3.2100        0.024918   
GRMN     29367439360  152.840    598371   2.5000        0.016357   
HD      348377153536  327.650   3746703   6.3000        0.019228   
HON     160165658624  231.990   3104555   3.6900        0.015906   
HRL      25927448576   47.830   2002620   0.9675        0.020228   
HSY      37023305728  178.860    908839   3.2160        0.017981   
INTC    213580759040   52.645  24522820   1.7025        0.032339   
IPG      13930211328   35.390   4076736   1.0500        0.029669   
ITW      72062394368  228.130    925960   4.5600        0.019989   
JNJ     453708480512  172.290   6667219   4.0900        0.023739   
KMB      45789528064  135.970   2445196   4.4200        0.032507   
KO      247213801472   57.290  14542633   1.6600        0.028975   
KR       29698973696   39.745   7887769   0.7200        0.018115   
LHX      46914686976  228.870   1074403   3.7400        0.016341   
LMT     104158552064  374.760   1168814  10.2000        0.027217   
LNC      11706035200   61.490   1331134   2.0600        0.033501   
LNT      14848014336   59.360   1363477   1.9685        0.033162   
MCD     183499112448  245.920   2442638   5.1200        0.020820   
MDLZ     91811848192   65.360   6530452   1.2600        0.019278   
NEM      48698736640   60.940   6756912   1.7500        0.028717   

        fiveYDividendperShareGrowthPerShare  \
symbol                                        
FMC                                1.722041   
GLW                                0.851758   
GPC                                0.293500   
GRMN                               0.195537   
HD                                 1.530625   
HON                                0.682067   
HRL                                0.953839   
HSY                                0.414704   
INTC                               0.428825   
IPG                                1.136301   
ITW                                1.160312   
JNJ                                0.350118   
KMB                                0.219428   
KO                                 0.240311   
KR                                 0.733318   
LHX                                0.680481   
LMT                                0.587158   
LNC                                0.923522   
LNT                                0.385541   
MCD                                0.415998   
MDLZ                               0.884854   
NEM                                9.231577   

        threeYDividendperShareGrowthPerShare  dividendYielPercentageTTM  \
symbol                                                                    
FMC                                 1.660358                   1.765258   
GLW                                 0.418052                   2.267127   
GPC                                 0.168611                   2.492236   
GRMN                                0.156973                   1.635697   
HD                                  0.688442                   1.922373   
HON                                 0.339004                   1.590586   
HRL                                 0.411464                   2.023424   
HSY                                 0.239925                   1.798758   
INTC                                0.272367                   3.233618   
IPG                                 0.422455                   2.958163   
ITW                                 0.593256                   1.998685   
JNJ                                 0.172206                   2.374594   
KMB                                 0.107968                   3.250717   
KO                                  0.105971                   2.897286   
KR                                  0.395665        

In [8]:
data3 =high_div(group3)

In [9]:
data3

mktCap    price   volAvg  lastDiv  dividend_yield  \
symbol                                                            
OMC      15711817728   73.280  1705000   2.7000        0.036845   
PEG      31557115904   62.430  1998801   2.0000        0.032036   
PEP     218000195584  157.730  4901287   4.1440        0.026273   
PG      345530925056  141.135  8434742   3.3215        0.023534   
PKG      13266875392  139.660   554006   3.7900        0.027137   
PPG      39225614336  165.260  1134628   2.7500        0.016640   
PRU      39784148992  100.975  1898663   4.5000        0.044565   
QCOM    157762076672  139.860  8048952   2.6300        0.018805   
RHI      10630736896   94.260   829685   1.4400        0.015277   
SJM      14348753920  132.415   835538   3.6000        0.027187   
SNA      11899685888  220.485   420396   4.7700        0.021634   
SRE      39961423872  131.990  1633557   4.2900        0.032502   
STX      19072538624   84.020  2982319   2.6600        0.031659   
TXN     170258382848  184.420  4269660   4.9800        0.027004   
WBA      40996061184   47.395  5726968   1.8715        0.039487   
WEC      30253373440   95.910  1179680   2.6215        0.027333   
WU        9576497152   23.400  3988088   0.9200        0.039316   
XEL      37238542336   69.190  2498306   1.7755        0.025661   
YUM      37085691904  124.490  1605701   1.9400        0.015584   

        fiveYDividendperShareGrowthPerShare  \
symbol                                        
OMC                                0.284348   
PEG                               -0.777760   
PEP                                0.451557   
PG                                 0.184654   
PKG                                0.367007   
PPG                                0.481761   
PRU                               -4.996765   
QCOM                               0.445056   
RHI                                0.696259   
SJM                                0.334261   
SNA                                1.035637   
SRE                                0.745764   
STX                                0.280483   
TXN                                1.605115   
WBA                                0.519693   
WEC                                0.508095   
WU                                 0.455899   
XEL                                0.359705   
YUM                                0.136057   

        threeYDividendperShareGrowthPerShare  dividendYielPercentageTTM  \
symbol                                                                    
OMC                                 0.177890                   3.686007   
PEG                                -0.798451                   3.201537   
PEP                                 0.272058                   2.626941   
PG                                  0.120100                   2.352504   
PKG                                 0.243077                   2.713733   
PPG                                 0.233920                   1.663743   
PRU                                -4.289870                   4.451919   
QCOM                                0.163413                   1.878571   
RHI                                 0.420914                   1.527851   
SJM                                 0.146975                   2.718725   
SNA                                 0.510443                   2.163412   
SRE                                 0.471779                   3.250000   
STX                                 0.369059                   3.168175   
TXN                                 0.752087                   2.702996   
WBA                                 0.256149                   3.946647   
WEC                                 0.217852                   2.732437   
WU                                  0.291799                   3.931624   
XEL                                 0.146689                   2.565381   
YUM                                 0.561548                   1.558358   

        payoutRatioTTM  avg_div3y  avgdiv5

In [11]:
strategy1_signal = pd.concat([data1, data2, data3],axis =0)

In [12]:
strategy1_signal

mktCap    price   volAvg  lastDiv  dividend_yield  \
symbol                                                           
ADI     59657768960  161.750  3196826   2.6200        0.016198   
ADM     32941070336   58.960  2594607   1.4600        0.024763   
ADP     88163082240  207.190  1569558   3.7000        0.017858   
AEE     21493284864   84.105  1322273   2.1100        0.025088   
AEP     43862007808   87.680  2812652   3.6600        0.041743   
...             ...      ...      ...      ...             ...   
WBA     40996061184   47.395  5726968   1.8715        0.039487   
WEC     30253373440   95.910  1179680   2.6215        0.027333   
WU       9576497152   23.400  3988088   0.9200        0.039316   
XEL     37238542336   69.190  2498306   1.7755        0.025661   
YUM     37085691904  124.490  1605701   1.9400        0.015584   

        fiveYDividendperShareGrowthPerShare  \
symbol                                        
ADI                                0.527875   
ADM                                0.260184   
ADP                                0.739091   
AEE                                0.213845   
AEP                               -0.995334   
...                                     ...   
WBA                                0.519693   
WEC                                0.508095   
WU                                 0.455899   
XEL                                0.359705   
YUM                                0.136057   

        threeYDividendperShareGrowthPerShare  dividendYielPercentageTTM  \
symbol                                                                    
ADI                                 0.396803                   1.619383   
ADM                                 0.110212                   2.475415   
ADP                                 0.535900                   1.785197   
AEE                                 0.132171                   2.508769   
AEP                                -0.995842                   4.174270   
...                                      ...                        ...   
WBA                                 0.256149                   3.946647   
WEC                                 0.217852                   2.732437   
WU                                  0.291799                   3.931624   
XEL                                 0.146689                   2.565381   
YUM                                 0.561548                   1.558358   

        payoutRatioTTM  avg_div3y  avgdiv5y  one_yearchange  
symbol                                                       
ADI           0.619189   2.186667     2.008        0.112903  
ADM           0.394271   1.393333     1.332        0.027778  
ADP           0.637348   3.106667     2.744        0.021978  
AEE           0.560317   1.903333     1.834        0.111111  
AEP           0.784200   2.653333     2.512        0.057143  
...                ...        ...       ...             ...  
WBA           0.707293   1.730000     1.626        0.021858  
WEC           0.656937   2.366667     2.232        0.071146  
WU            0.505625   0.820000     0.760        0.044444  
XEL           0.620272   1.620000     1.532        0.063953  
YUM           0.509102   1.666667     1.608        0.063830  

[67 rows x 12 columns]

In [14]:
strategy1_signal.to_csv(r'C:\Users\jizha\Desktop\seabridge_watchlist\high_dividend_list.csv' ) 